In [0]:
alreadyMounted=False

In [0]:
for x in dbutils.fs.mounts():
    if x.mountPoint=="/mnt/myazureproject":
        alreadyMounted=True
        print("Already Mounted")
        break
    else:
        alreadyMounted=False

Already Mounted


In [0]:
if not alreadyMounted:
    dbutils.fs.mount(
        source="wasbs://datasets@myprojectadlsgen2.blob.core.windows.net",
        mount_point="/mnt/myazureproject",
        extra_configs={"fs.azure.account.key.myprojectadlsgen2.blob.core.windows.net":"kmO9ccIgSpJ+d/XwtCd7WCxZSbl/jrWWxS3gE28j2GqIPdAN+mnKep6drQMbKtKDbFtNsbHRbKF++AStDgnB7w=="}
    )
    alreadyMounted=True
    print("Successfully Mounted")
else:
    print("Already Mounted.")

Already Mounted.


In [0]:
alreadyMounted1 = False

In [0]:
for x in dbutils.fs.mounts():
    if x.mountPoint=="/mnt/azueprojecterrorrecords":
        alreadyMounted1=True
        print("Already Mounted")
        break
    else:
        alreadyMounted1=False

Already Mounted


In [0]:
if not alreadyMounted1:
    dbutils.fs.mount(
        source="wasbs://errorrecords@myprojectadlsgen2.blob.core.windows.net",
        mount_point="/mnt/azueprojecterrorrecords",
        extra_configs={"fs.azure.account.key.myprojectadlsgen2.blob.core.windows.net":"kmO9ccIgSpJ+d/XwtCd7WCxZSbl/jrWWxS3gE28j2GqIPdAN+mnKep6drQMbKtKDbFtNsbHRbKF++AStDgnB7w=="}
    )
    alreadyMounted1=True
    print("Successfully Mounted")
else:
    print("Already Mounted.")

Already Mounted.


In [0]:
movie_raw_df = spark.read\
.format("avro")\
.load("/mnt/myazureproject/Movie/tmdb_5000_movies.avro")

In [0]:
movie_raw_df.createOrReplaceTempView("movie_raw")

In [0]:
movie_id_count_df = movie_raw_df\
.groupBy("id")\
.count()

In [0]:
error_movies_records = movie_id_count_df.filter("count!=1")

In [0]:
if error_movies_records.count()>0:
    error_movies_records.write\
    .format("csv")\
    .mode("append")\
    .option("path","/mnt/azueprojecterrorrecords")\
    .save()
    print("Error Records are written to the Data Lake.")
else:
    print("All the movie ids are unique and no error record was found.")

All the movie ids are unique and no error record was found.


In [0]:
error_movies_records.createOrReplaceTempView("error_movie_records")

In [0]:
movie_raw_df1 = spark.sql("SELECT * FROM movie_raw WHERE id NOT IN (SELECT id FROM error_movie_records)")

In [0]:
movie_raw_df1.createOrReplaceTempView("movie_raw1")

In [0]:
movie_crew_raw_df = spark.read\
.format("avro")\
.load("/mnt/myazureproject/MovieCrew/data_c6880b94-0a07-46ea-9020-889d0abb62a8_82f2601c-2559-4e36-8add-501cbc5ef72f.avro")

In [0]:
movie_crew_raw_df.createOrReplaceTempView("movie_crew_raw")

In [0]:
movie_crew_total_id_df = movie_crew_raw_df\
.groupBy("movie_id")\
.count()

In [0]:
movie_crew_errorrecords_df = movie_crew_total_id_df.filter("count!=1")

In [0]:
movie_crew_errorrecords_df.createOrReplaceTempView("movie_crew_errors")

In [0]:
if movie_crew_errorrecords_df.count()>1:
    movie_crew_errorrecords_df\
    .write\
    .format("csv")\
    .mode("append")\
    .mode("append")\
    .option("path","/mnt/azueprojecterrorrecords")\
    .save()
    print("Faulted records from movie crew are written to the Data Lake")
else:
    print("No faulty record was found.")

No faulty record was found.


In [0]:
movie_crew_raw_df1 = spark.sql("SELECT * FROM movie_crew_raw WHERE movie_id NOT IN (SELECT movie_id FROM movie_crew_errors)")

In [0]:
movie_crew_raw_df1.createOrReplaceTempView("movie_crew_raw1")

In [0]:
movie_not_in_master_file_df = spark.sql("SELECT * FROM movie_raw1 WHERE id NOT IN (SELECT movie_id FROM movie_crew_raw1)")

In [0]:
if movie_not_in_master_file_df.count()>0:
    movie_not_in_master_file_df\
    .write\
    .format("csv")\
    .mode("append")\
    .option("path","/mnt/azueprojecterrorrecords")\
    .save()
    print("Movie records not in master file are written to Data Lake.")
else:
    print("All movies are present in the master file.")

All movies are present in the master file.


In [0]:
movie_id_null = movie_raw_df1.filter("id IS NULL")

In [0]:
movie_id_null.createOrReplaceTempView("movie_idnull")

In [0]:
if movie_id_null.count()>0:
    movie_id_null\
    .write\
    .format("csv")\
    .mode("append")\
    .option("path","/mnt/azueprojecterrorrecords")\
    .save()
    print("Null movie IDs are written to Data Lake.")
else:
    print("No Movie ID is NULL.")

No Movie ID is NULL.


In [0]:
movie_raw_df2 = spark.sql("SELECT * FROM movie_raw1 WHERE id NOT IN (SELECT id FROM movie_idnull)")

In [0]:
joined_df = movie_raw_df2.join(movie_crew_raw_df1,movie_raw_df2.id==movie_crew_raw_df1.movie_id,"inner")\
.select("movie_id","movie_title","budget","homepage","original_language","popularity","release_date","revenue","runtime","status","vote_average","vote_count")

In [0]:
from pyspark.sql.types import *
from pyspark.sql.functions import *

In [0]:
display(joined_df)

movie_id movie_title budget homepage original_language popularity release_date revenue runtime status vote_average vote_count 19995 Avatar 237000000 http://www.avatarmovie.com/ en 150.437577 10-12-2009 2787965087 162 Released 7.2 11800 285 Pirates of the Caribbean: At World's End 300000000 http://disney.go.com/disneypictures/pirates/ en 139.082615 19-05-2007 961000000 169 Released 6.9 4500 206647 Spectre 245000000 http://www.sonypictures.com/movies/spectre/ en 107.376788 26-10-2015 880674609 148 Released 6.3 4466 49026 The Dark Knight Rises 250000000 http://www.thedarkknightrises.com/ en 112.31295 16-07-2012 1084939099 165 Released 7.6 9106 49529 John Carter 260000000 http://movies.disney.com/john-carter en 43.926995 07-03-2012 284139100 132 Released 6.1 2124 559 Spider-Man 3 258000000 http://www.sonypictures.com/movies/spider-man3/ en 115.699814 01-05-2007 890871626 139 Released 5.9 3576 38757 Tangled 260000000 http://disney.go.com/disneypictures/tangled/ en 48.681969 24-11-2010 591794936 100 Released 7.4 3330 99861 Avengers: Age of Ultron 280000000 http://marvel.com/movies/movie/193/avengers_age_of_ultron en 134.279229 22-04-2015 1405403694 141 Released 7.3 6767 767 Harry Potter and the Half-Blood Prince 250000000 http://harrypotter.warnerbros.com/harrypotterandthehalf-bloodprince/dvd/index.html en 98.885637 07-07-2009 933959197 153 Released 7.4 5293 209112 Batman v Superman: Dawn of Justice 250000000 http://www.batmanvsupermandawnofjustice.com/ en 155.790452 23-03-2016 873260194 151 Released 5.7 7004 1452 Superman Returns 270000000 http://www.superman.com en 57.925623 28-06-2006 391081192 154 Released 5.4 1400 10764 Quantum of Solace 200000000 http://www.mgm.com/view/movie/234/Quantum-of-Solace/ en 107.928811 30-10-2008 586090727 106 Released 6.1 2965 58 Pirates of the Caribbean: Dead Man's Chest 200000000 http://disney.go.com/disneypictures/pirates/ en 145.847379 20-06-2006 1065659812 151 Released 7 5246 57201 The Lone Ranger 255000000 http://disney.go.com/the-lone-ranger/ en 49.046956 03-07-2013 89289910 149 Released 5.9 2311 49521 Man of Steel 225000000 http://www.manofsteel.com/ en 99.398009 12-06-2013 662845518 143 Released 6.5 6359 2454 The Chronicles of Narnia: Prince Caspian 225000000 null en 53.978602 15-05-2008 419651413 150 Released 6.3 1630 24428 The Avengers 220000000 http://marvel.com/avengers_movie/ en 144.448633 25-04-2012 1519557910 143 Released 7.4 11776 1865 Pirates of the Caribbean: On Stranger Tides 380000000 http://disney.go.com/pirates/index-on-stranger-tides.html#/video/ en 135.413856 14-05-2011 1045713802 136 Released 6.4 4948 41154 Men in Black 3 225000000 http://www.sonypictures.com/movies/meninblack3/ en 52.035179 23-05-2012 624026776 106 Released 6.2 4160 122917 The Hobbit: The Battle of the Five Armies 250000000 http://www.thehobbit.com/ en 120.965743 10-12-2014 956019788 144 Released 7.1 4760 1930 The Amazing Spider-Man 215000000 http://www.theamazingspiderman.com en 89.866276 27-06-2012 752215857 136 Released 6.5 6586 20662 Robin Hood 200000000 http://www.robinhoodthemovie.com/ en 37.668301 12-05-2010 310669540 140 Released 6.2 1398 57158 The Hobbit: The Desolation of Smaug 250000000 http://www.thehobbit.com/ en 94.370564 11-12-2013 958400000 161 Released 7.6 4524 2268 The Golden Compass 180000000 http://www.goldencompassmovie.com/index_german.html en 42.990906 04-12-2007 372234864 113 Released 5.8 1303 254 King Kong 207000000 null en 61.22601 14-12-2005 550000000 187 Released 6.6 2337 597 Titanic 200000000 http://www.titanicmovie.com en 100.025899 18-11-1997 1845034188 194 Released 7.5 7562 271110 Captain America: Civil War 250000000 http://marvel.com/captainamericapremiere en 198.372395 27-04-2016 1153304495 147 Released 7.1 7241 44833 Battleship 209000000 null en 64.928382 11-04-2012 303025485 131 Released 5.5 2114 135397 Jurassic World 150000000 http://www.jurassicworld.com/ en 418.708552 09-06-2015 1513528810 124 Released 6.5 8662 37724 Skyfall 200000000 http://www.skyfall-movie.com en 9

In [0]:
joined_datatypecorrected_df = joined_df\
.withColumn("movie_id",joined_df.movie_id.cast(LongType()))\
.withColumn("budget",joined_df["budget"].cast("Long"))\
.withColumn("popularity",joined_df.popularity.cast(FloatType()))\
.withColumn("release_date",to_date("release_date","dd-MM-yyyy"))\
.withColumn("revenue",joined_df.revenue.cast(LongType()))\
.withColumn("vote_average",joined_df.vote_average.cast(FloatType()))\
.withColumn("vote_count",joined_df["vote_count"].cast("Long"))

In [0]:
display(joined_datatypecorrected_df)

movie_id movie_title budget homepage original_language popularity release_date revenue runtime status vote_average vote_count 19995 Avatar 237000000 http://www.avatarmovie.com/ en 150.43758 2009-12-10 2787965087 162 Released 7.2 11800 285 Pirates of the Caribbean: At World's End 300000000 http://disney.go.com/disneypictures/pirates/ en 139.08261 2007-05-19 961000000 169 Released 6.9 4500 206647 Spectre 245000000 http://www.sonypictures.com/movies/spectre/ en 107.376785 2015-10-26 880674609 148 Released 6.3 4466 49026 The Dark Knight Rises 250000000 http://www.thedarkknightrises.com/ en 112.31295 2012-07-16 1084939099 165 Released 7.6 9106 49529 John Carter 260000000 http://movies.disney.com/john-carter en 43.926994 2012-03-07 284139100 132 Released 6.1 2124 559 Spider-Man 3 258000000 http://www.sonypictures.com/movies/spider-man3/ en 115.699814 2007-05-01 890871626 139 Released 5.9 3576 38757 Tangled 260000000 http://disney.go.com/disneypictures/tangled/ en 48.68197 2010-11-24 591794936 100 Released 7.4 3330 99861 Avengers: Age of Ultron 280000000 http://marvel.com/movies/movie/193/avengers_age_of_ultron en 134.27924 2015-04-22 1405403694 141 Released 7.3 6767 767 Harry Potter and the Half-Blood Prince 250000000 http://harrypotter.warnerbros.com/harrypotterandthehalf-bloodprince/dvd/index.html en 98.885635 2009-07-07 933959197 153 Released 7.4 5293 209112 Batman v Superman: Dawn of Justice 250000000 http://www.batmanvsupermandawnofjustice.com/ en 155.79045 2016-03-23 873260194 151 Released 5.7 7004 1452 Superman Returns 270000000 http://www.superman.com en 57.925625 2006-06-28 391081192 154 Released 5.4 1400 10764 Quantum of Solace 200000000 http://www.mgm.com/view/movie/234/Quantum-of-Solace/ en 107.92881 2008-10-30 586090727 106 Released 6.1 2965 58 Pirates of the Caribbean: Dead Man's Chest 200000000 http://disney.go.com/disneypictures/pirates/ en 145.84738 2006-06-20 1065659812 151 Released 7.0 5246 57201 The Lone Ranger 255000000 http://disney.go.com/the-lone-ranger/ en 49.046955 2013-07-03 89289910 149 Released 5.9 2311 49521 Man of Steel 225000000 http://www.manofsteel.com/ en 99.39801 2013-06-12 662845518 143 Released 6.5 6359 2454 The Chronicles of Narnia: Prince Caspian 225000000 null en 53.978603 2008-05-15 419651413 150 Released 6.3 1630 24428 The Avengers 220000000 http://marvel.com/avengers_movie/ en 144.44864 2012-04-25 1519557910 143 Released 7.4 11776 1865 Pirates of the Caribbean: On Stranger Tides 380000000 http://disney.go.com/pirates/index-on-stranger-tides.html#/video/ en 135.41385 2011-05-14 1045713802 136 Released 6.4 4948 41154 Men in Black 3 225000000 http://www.sonypictures.com/movies/meninblack3/ en 52.03518 2012-05-23 624026776 106 Released 6.2 4160 122917 The Hobbit: The Battle of the Five Armies 250000000 http://www.thehobbit.com/ en 120.965744 2014-12-10 956019788 144 Released 7.1 4760 1930 The Amazing Spider-Man 215000000 http://www.theamazingspiderman.com en 89.86628 2012-06-27 752215857 136 Released 6.5 6586 20662 Robin Hood 200000000 http://www.robinhoodthemovie.com/ en 37.6683 2010-05-12 310669540 140 Released 6.2 1398 57158 The Hobbit: The Desolation of Smaug 250000000 http://www.thehobbit.com/ en 94.37057 2013-12-11 958400000 161 Released 7.6 4524 2268 The Golden Compass 180000000 http://www.goldencompassmovie.com/index_german.html en 42.990906 2007-12-04 372234864 113 Released 5.8 1303 254 King Kong 207000000 null en 61.22601 2005-12-14 550000000 187 Released 6.6 2337 597 Titanic 200000000 http://www.titanicmovie.com en 100.0259 1997-11-18 1845034188 194 Released 7.5 7562 271110 Captain America: Civil War 250000000 http://marvel.com/captainamericapremiere en 198.37239 2016-04-27 1153304495 147 Released 7.1 7241 44833 Battleship 209000000 null en 64.92838 2012-04-11 303025485 131 Released 5.5 2114 135397 Jurassic World 150000000 http://www.jurassicworld.com/ en 418.70856 2015-06-09 1513528810 124 Released 6.5 8662 37724 Skyfall 200000000 http://www.skyfall-movie.com en 93.00499 2012-10-25

In [0]:
joined_datatypecorrected_df.createOrReplaceTempView("tempviewformoviesilver")

In [0]:
%sql
CREATE DATABASE IF NOT EXISTS azureproject_db;

In [0]:
%sql
CREATE TABLE IF NOT EXISTS azureproject_db.movie_silver
(
movie_id INTEGER,
movie_title VARCHAR(100),
budget LONG NOT NULL,
homepage VARCHAR(2000),
original_language VARCHAR(10),
popularity FLOAT,
release_date DATE,
revenue DOUBLE,
runtime INTEGER,
status VARCHAR(20),
vote_average FLOAT,
vote_count INTEGER
) TBLPROPERTIES (delta.enableChangeDataFeed=True);

In [0]:
%sql
MERGE INTO azureproject_db.movie_silver AS T USING tempviewformoviesilver AS S ON T.movie_id=S.movie_id
WHEN MATCHED THEN UPDATE SET T.popularity=S.popularity,T.revenue=S.revenue,T.status=S.status,T.vote_average=S.vote_average,T.vote_count=S.vote_count
WHEN NOT MATCHED THEN
INSERT (movie_id,movie_title,budget,homepage,original_language,popularity,release_date,revenue,runtime,status,vote_average,vote_count)
VALUES(S.movie_id,S.movie_title,S.budget,S.homepage,S.original_language,S.popularity,S.release_date,S.revenue,S.runtime,S.status,S.vote_average,S.vote_count)

num_affected_rows num_updated_rows num_deleted_rows num_inserted_rows 4803 4803 0 0

In [0]:
dbServer_Name = "myproject-server"
dbPort_Number = "1433"
dbName = "myproject-db"
dbUserName = "ganesh"
dbPassword = "gane9975#"

In [0]:
connectionUrl = 'jdbc:sqlserver://{}.database.windows.net:{};database={};user={};'.format(dbServer_Name,dbPort_Number,dbName,dbUserName)

In [0]:
connectionProperties = {'password': dbPassword,'driver':'com.microsoft.sqlserver.jdbc.SQLServerDriver'}

In [0]:
movie_silver_df = spark.read.table("azureproject_db.movie_silver")

In [0]:
movie_silver_df\
.write\
.jdbc(url=connectionUrl,table="dbo.movie_final",properties=connectionProperties,mode="overwrite")

In [0]:
alreadyMounted2 = False

In [0]:
for x in  dbutils.fs.mounts():
    if x.mountPoint=="/mnt/output":
        alreadyMounted2=True
        print("Already Mounted.")
        break
    else:
        alreadyMounted2=False

In [0]:
if not alreadyMounted2:
    dbutils.fs.mount(
        source="wasbs://output@myprojectadlsgen2.blob.core.windows.net",
        mount_point="/mnt/output",
        extra_configs={"fs.azure.account.key.myprojectadlsgen2.blob.core.windows.net":"kmO9ccIgSpJ+d/XwtCd7WCxZSbl/jrWWxS3gE28j2GqIPdAN+mnKep6drQMbKtKDbFtNsbHRbKF++AStDgnB7w=="}
    )
    alreadyMounted2=True
    print("Successfully Mounted.")
else:
    print("Already Mounted.")

Successfully Mounted.


In [0]:
budget_zero_movies_df = movie_silver_df.filter("budget=0")

In [0]:
budget_zero_movies_df\
.write\
.format("parquet")\
.mode("overwrite")\
.option("path","mnt/output/ZeroBudgetMovies")\
.save()

In [0]:
non_zero_budget_movies_df = movie_silver_df.filter("budget>0")

In [0]:
non_zero_budget_movies_df\
.write\
.mode("overwrite")\
.option("path","/mnt/output/NonZeroBudgetMovies")\
.save()